In [8]:
import pandas as pd
from matplotlib import pyplot as plt
import numpy as np
from wordcloud import WordCloud

import spacy
from spacy.lang.pt.stop_words import STOP_WORDS
from spacy.tokens import DocBin

import json
import re
import string
from stop_words import get_stop_words
import os

import math

from sklearn.model_selection import train_test_split
from sklearn.model_selection import StratifiedShuffleSplit, StratifiedKFold

from imblearn.over_sampling import RandomOverSampler



In [11]:
pd.set_option("display.max_colwidth", 255)
pd.set_option('display.max_rows', 255)

In [ ]:
df = pd.read_excel("lemma-mapping23-nltk.xlsx")
cnt = df.groupby("CASISTICA_MOTIVAZIONE").count() \
.rename(columns={"Unnamed: 0": "count"})["count"]



In [ ]:
run_count = 0

In [27]:
"""class_dict = {"Doc. sanitaria scaduta" : 20, 
            "Esenzione per ultratrentennale" : 20, 
            "Variazioni tecniche" : 20, 
            "Furto tardivo" : 20, 
            "Rientro ecoincentivo" : 20, 
            "Rateizzazione" : 20, 
            "EREDI" : 20, 
            "Domiciliazione assente" : 20, 
            "Esenzione successiva" : 20, 
            "Ecoincentivo" : 20, 
            "Versamento annullato" : 20, 
            "Storico" : 20, 
            "Esenzione PH eredi" : 20, 
            "No minivoltura" : 20, 
            "Perdita possesso con DS" : 20, 
            "Rientro in possesso" : 20, 
            "Esenzione PH o storica successiva" : 20
            }"""

class_dict = {"Doc. sanitaria scaduta" : 3, 
            "Esenzione per ultratrentennale" : 3, 
            "Variazioni tecniche" : 3, 
            "Furto tardivo" : 3,
            "Rientro ecoincentivo" :3
            }
oversample = RandomOverSampler(sampling_strategy=class_dict)

X_over, y_over = oversample.fit_resample(df[["NOTE_OPERATORE", "CASISTICA_LAVORAZIONE"]].to_numpy(), df["CASISTICA_MOTIVAZIONE"].to_numpy())
df_over = pd.DataFrame({"NOTE_OPERATORE":X_over[:,0], "CASISTICA_LAVORAZIONE":X_over[:,1],"CASISTICA_MOTIVAZIONE":y_over})

sss = StratifiedShuffleSplit(n_splits=1, test_size=0.3, random_state=0)
#sss = StratifiedKFold(n_splits=2, shuffle=True, random_state=0)

sss_val = StratifiedShuffleSplit(n_splits=1, test_size=0.33, random_state=0)


for i, (train_val_index, test_index) in enumerate(sss.split(X_over,  y_over)):
    train_val_index_df = df_over.iloc[train_val_index]
    test_index_df = df_over.iloc[test_index]

for i, (train_index, val_index) in enumerate(sss_val.split(train_val_index_df[["NOTE_OPERATORE", "CASISTICA_LAVORAZIONE"]],  train_val_index_df["CASISTICA_MOTIVAZIONE"])):
    train_index_df = train_val_index_df.iloc[train_index]
    val_index_df = train_val_index_df.iloc[val_index]

In [ ]:
for i in ["Doc. sanitaria scaduta", "Esenzione per ultratrentennale", "Variazioni tecniche", "Furto tardivo", "Rientro ecoincentivo", "Rateizzazione", "EREDI", "Domiciliazione assente"]:
    print("I: {}".format(i))
    print(train_index_df[train_index_df["CASISTICA_MOTIVAZIONE"] == i])
    print("-------------------------------------------------")


In [ ]:
X_train, X_test, y_train, y_test = train_test_split(X_over, y_over, test_size=0.2, random_state=1)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2, random_state=1)

train_df = pd.DataFrame({"NOTE_OPERATORE":X_train[:,0], "CASISTICA_MOTIVAZIONE":y_train})
test_df = pd.DataFrame({"NOTE_OPERATORE":X_test[:,0], "CASISTICA_MOTIVAZIONE":y_test})
val_df = pd.DataFrame({"NOTE_OPERATORE":X_val[:,0], "CASISTICA_MOTIVAZIONE":y_val})

In [166]:
tmp = pd.DataFrame({"col":test_index_df["CASISTICA_MOTIVAZIONE"]})
tmp["C"]=1
tmp.groupby("col").count().size

34

In [31]:
def add_casistica_lavorazione(orig_df):
    res_df = orig_df.copy()
    res_df["C"] = res_df.apply(lambda row: row["CASISTICA_LAVORAZIONE"] in row["input_doc"], axis=1)
    res_df["input_doc"] =np.where(res_df["C"], res_df["NOTE_OPERATORE"],res_df["NOTE_OPERATORE"] + " " + res_df["CASISTICA_LAVORAZIONE"])
    res_df = res_df.drop("C", axis=1)
    return res_df

def replace_punct(text):
    text = ''.join([char for char in text if char not in string.punctuation])
    return text

def remove_stopwords(text):
    ita_stop_words = get_stop_words('italian')
    pattern = r'\b(?:' + '|'.join(re.escape(s) for s in ita_stop_words) + r')\b'
    return re.sub(pattern, '', text)

def transform_df(orig_df):
    res_df = orig_df.copy()
    res_df["input_doc"] = res_df["NOTE_OPERATORE"]
    #res_df = add_casistica_lavorazione(res_df)

    #res_df["input_doc"] = res_df["input_doc"].apply(lambda x: remove_stopwords(x))
    #res_df["input_doc"] = res_df["input_doc"].apply(lambda x: replace_punct(x))
    return res_df



In [ ]:

def convert(input_df, outfile):
    
    nlp = spacy.load("it_core_news_md")
    #nlp = spacy.blank("it")
    
    db = DocBin()
      
    categories = input_df["CASISTICA_MOTIVAZIONE"].drop_duplicates().to_list()

    for index, row in input_df.iterrows():

        row_doc = row["input_doc"]
        doc = nlp.make_doc(row_doc)
        doc.cats = {category: 0 for category in categories}
        doc.cats[row["CASISTICA_MOTIVAZIONE"]] = 1
        db.add(doc)
    db.to_disk(outfile)



In [36]:
run_count+=1
run = "run_{}".format(run_count)


In [38]:
spacy_data_path = "C:\\Users\\a.torchi\\Desktop\\text_classification\\spacy\\spacy_data\\{}".format(run)
if(not os.path.exists(spacy_data_path)):
   os.mkdir(spacy_data_path)

spacy_result_path = "C:\\Users\\a.torchi\\Desktop\\text_classification\\spacy\\spacy_result\\{}".format(run)
if(not os.path.exists(spacy_result_path)):
   os.mkdir(spacy_result_path)

convert(transform_df(train_index_df), os.path.join(spacy_data_path, "train.spacy"))
convert(transform_df(test_index_df), os.path.join(spacy_data_path, "test.spacy"))
convert(transform_df(val_index_df), os.path.join(spacy_data_path, "val.spacy"))


In [33]:
!python -m spacy init config --lang it --pipeline textcat spacy/config.cfg --force


ℹ Generated config template specific for your use case
- Language: it
- Pipeline: textcat
- Optimize for: efficiency
- Hardware: CPU
- Transformer: None
✔ Auto-filled config with all values
✔ Saved config
spacy\config.cfg
You can now add your data and train your pipeline:
python -m spacy train config.cfg --paths.train ./train.spacy --paths.dev ./dev.spacy


In [39]:
!python -m spacy train spacy/config.cfg --paths.train ./spacy/spacy_data/{run}/train.spacy  --paths.dev ./spacy/spacy_data/{run}/val.spacy --output spacy/spacy_result/{run}/textcat_model
!python -m spacy evaluate ./spacy/spacy_result/{run}/textcat_model/model-best/ --output ./spacy/spacy_result/{run}/metrics.json ./spacy/spacy_data/{run}/test.spacy

✔ Created output directory: spacy\spacy_result\run_9\textcat_model
ℹ Saving to output directory:
spacy\spacy_result\run_9\textcat_model
ℹ Using CPU

=========================== Initializing pipeline ===========================
✔ Initialized pipeline

============================= Training pipeline =============================
ℹ Pipeline: ['textcat']
ℹ Initial learn rate: 0.001
E    #       LOSS TEXTCAT  CATS_SCORE  SCORE 
---  ------  ------------  ----------  ------
  0       0          0.03        6.37    0.06
  1     200          5.12        9.25    0.09
  3     400          3.61       11.22    0.11
  6     600          2.68       16.08    0.16
  9     800          2.08       19.02    0.19
 12    1000          1.66       23.11    0.23
 17    1200          1.37       28.34    0.28
 23    1400          1.11       31.72    0.32
 29    1600          0.92       36.20    0.36
 38    1800          0.77       39.51    0.40
 48    2000          0.64       38.71    0.39
 60    2200          